# Eric Eaton and Sam Haines

# Final Project Submission Code

# Step 1: Feature Extraction
### Ensure that all uploaded csv files submitted on canvas are in the same directoy as the python files
### The 'exampleDataset' was included to show to ability of the program on a small portion of the dataset. 
### The rest of the code in this file uses the full dataset

In [1]:
import os
from imageio import imread
import numpy as np
import pandas as pd
from tqdm import tqdm
from sklearn.decomposition import PCA

class ImageToCSV:

    def __init__(self,dataset):
        self.dataset = dataset
        self.positiveCount, self.negativeCount, self.unusableCount, self.totalCount,\
        self.arrayImages,self.filenames, self.classList = self.image_to_array(self.dataset)
        self.entries = self.featureExtractor(self.arrayImages,self.classList,self.filenames,self.totalCount)
        self.dataFrame = pd.DataFrame(self.entries)
        self.dataFrame.to_csv('ExamppleCancerImagesSVD.csv',index=False)


    def image_to_array(self,dataset):
        arrayImages = []
        classList = []
        names = []
        pc = 0
        nc = 0
        uc = 0
        count = 0
        print("\nConverting Images to an Array\n")
        for (rootDir, dirNames, filenames) in os.walk(dataset):
            for filename in filenames:
                if filename == "":
                    continue
                count = count + 1
        progressBar = tqdm(total=count)
        for (rootDir, dirNames, filenames) in os.walk(dataset):
            for filename in filenames:
                loadedImage = imread(os.path.join(rootDir,filename))
                if loadedImage.shape == (50,50,3):
                    arrayImages.append(loadedImage)
                    names.append(filename)
                    if filename[-5] == '0':
                        nc = nc+1
                        classList.append(0)
                    if filename[-5] == '1':
                        pc = pc+1
                        classList.append(1)
                else:
                    uc = uc +1
                progressBar.update(1)

        count = count - uc
        return pc, nc, uc, count, arrayImages,names,classList


    def featureExtractor(self, arrayImages,classList, filenames,count, in_features = 50):
        pca = PCA(n_components=in_features)
        index= 0
        entries = []
        progressBar = tqdm(total=count)
        print("\nExtracting Features\n")
        for array in arrayImages:
            condensedImage = self.condenser(array)
            pca.fit(condensedImage)
            features = pca.singular_values_
            features = np.append(features,classList[index])
            features = np.append(features,filenames[index])
            index = index + 1
            entries.append(features)
            progressBar.update(1)
        return entries

    def condenser(self, image):
        condensedImage = (image[:, :, 0] + image[:, :, 1] + image[:, :, 2])
        return condensedImage


data = ImageToCSV('exampleDataset')


Converting Images to an Array



100%|███████████████████████████████████████████████████████████████████████████████| 100/100 [00:00<00:00, 805.72it/s]


Extracting Features



# Step 2: Feature Selection
#### Note: The dataset was pruned manually during each iteration, so only the first and final iterations are included

In [2]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.svm import LinearSVC
from sklearn.model_selection import StratifiedKFold
from sklearn.feature_selection import RFECV
from matplotlib import pyplot as plt

#-------------------------------LR First Iteration -----------------------------------

data = pd.read_csv('CancerImagesSingularValues.csv',header=0)
X = np.array(data.iloc[:,0:50])
y = np.array(data['50'])
sc = StandardScaler()
X = sc.fit_transform(X)
model = LogisticRegression(n_jobs=-1,max_iter = 10000)
rfecvLR = RFECV(estimator=model, step=1, cv=StratifiedKFold(2),scoring="accuracy",min_features_to_select=1,n_jobs=-1)
print("Starting First Iteration LR")
rfecvLR.fit(X,y)
print("Done First Iteration LR")

#---------------------SVM First Iteration--------------------------------

X = np.array(data.iloc[:,0:50])
y = np.array(data['50'])
sc = StandardScaler()
X = sc.fit_transform(X)
model = LinearSVC(max_iter=100000)
rfecvSVM = RFECV(estimator=model, step=1, cv=StratifiedKFold(2),scoring="accuracy",min_features_to_select=1,n_jobs=-1)
print("Starting First Iteration SVM")
rfecvSVM.fit(X,y)
print("Done First Iteration sVM")

#----------------------------------------------LR Final Iteration----------------------------------------

data = pd.read_csv('CancerImagesSingularValuesRFELR2.csv',header=0)
X = np.array(data.iloc[:,0:25])
y = np.array(data['25'])
sc = StandardScaler()
X = sc.fit_transform(X)
model = LogisticRegression(n_jobs=-1,max_iter = 10000)
rfecvLR2 = RFECV(estimator=model, step=1, cv=StratifiedKFold(2),scoring="accuracy",min_features_to_select=1,n_jobs=-1)
print("Starting Final Iteration LR")
rfecvLR2.fit(X,y)
print("Done Final Iteration LR")

#---------------------SVM Final Iteration--------------------------------

data = pd.read_csv('CancerImagesSVDRFE5.csv',header=0)
X = np.array(data.iloc[:,0:16])
y = np.array(data['16'])
sc = StandardScaler()
X = sc.fit_transform(X)
model = LinearSVC(max_iter=100000)
print("Starting Final Iteration SVM")
rfecvSVM2 = RFECV(estimator=model, step=1, cv=StratifiedKFold(2),scoring="accuracy",min_features_to_select=1,n_jobs=-1)
rfecvSVM2.fit(X,y)
print("Done Final Iteration SVM")

#--------------------- PLOT FIGURE ------------------------------------

plt.figure(dpi=1080,figsize =(16,9))
plt.subplot(221)
plt.plot(range(1, len(rfecvLR.grid_scores_) + 1), rfecvLR.grid_scores_, color='orange')
plt.title('Linear Regression First Iteration',size=20)
plt.xlabel("Number of Features Selected", size = 18)
plt.ylabel("Accuracy", size= 18)
plt.suptitle("Recursive Feature Elimination", size = 25)
plt.xticks(fontsize=15)
plt.yticks(fontsize =15)
plt.subplot(222)
plt.plot(range(1, len(rfecvLR2.grid_scores_) + 1), rfecvLR2.grid_scores_, color='orange')
plt.title('Linear Regression Final Iteration',size=20)
plt.xlabel("Number of Features Selected", size = 18)
plt.ylabel("Accuracy", size = 18)
plt.xticks(fontsize=15)
plt.yticks(fontsize =15)
plt.subplots_adjust(hspace=0.5)
plt.subplot(223)
plt.plot(range(1, len(rfecvSVM.grid_scores_) + 1), rfecvSVM.grid_scores_, color='purple')
plt.title('Support Vector Machine First Iteration',size=20)
plt.xlabel("Number of Features Selected", size = 18)
plt.ylabel("Accuracy", size = 18)
plt.xticks(fontsize=15)
plt.yticks(fontsize =15)
plt.subplots_adjust(hspace=0.5)
plt.subplot(224)
plt.plot(range(1, len(rfecvSVM2.grid_scores_) + 1), rfecvSVM2.grid_scores_, color='purple')
plt.title('Support Vector Machine Final Iteration',size=20)
plt.xlabel("Number of Features Selected", size = 18)
plt.ylabel("Accuracy", size = 18)
plt.xticks(fontsize=15)
plt.yticks(fontsize =15)
plt.subplots_adjust(hspace=0.5)

Starting First Iteration LR
Done First Iteration LR
Starting First Iteration SVM
Done First Iteration sVM
Starting Final Iteration LR
Done Final Iteration LR
Starting Final Iteration SVM
Done Final Iteration SVM


c:\users\eric eaton\appdata\local\programs\python\python39\lib\site-packages\sklearn\utils\deprecation.py:103: FutureWarning: The `grid_scores_` attribute is deprecated in version 1.0 in favor of `cv_results_` and will be removed in version 1.2.
  warnings.warn(msg, category=FutureWarning)
c:\users\eric eaton\appdata\local\programs\python\python39\lib\site-packages\sklearn\utils\deprecation.py:103: FutureWarning: The `grid_scores_` attribute is deprecated in version 1.0 in favor of `cv_results_` and will be removed in version 1.2.
  warnings.warn(msg, category=FutureWarning)
c:\users\eric eaton\appdata\local\programs\python\python39\lib\site-packages\sklearn\utils\deprecation.py:103: FutureWarning: The `grid_scores_` attribute is deprecated in version 1.0 in favor of `cv_results_` and will be removed in version 1.2.
  warnings.warn(msg, category=FutureWarning)
c:\users\eric eaton\appdata\local\programs\python\python39\lib\site-packages\sklearn\utils\deprecation.py:103: FutureWarning: T

# Step 3: Accuracy Metrics for Machine Learning Algorithms

## 3a. K-Nearest Neighbors

In [4]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix as cm
from sklearn.metrics import accuracy_score as acc
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from statistics import mean
from sklearn.preprocessing import StandardScaler

dataLR = pd.read_csv('CancerImagesSingularValuesRFELR2.csv')
dataSVM = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')
#Cross Validation Function
cv = KFold(n_splits=5,random_state=1,shuffle=True)
#Assign Training and testing data
X1 = np.array(dataSVM.iloc[:,0:16])
y1 = np.array(dataSVM['16'])

X2 = np.array(dataLR.iloc[:,0:25])
y2 = np.array(dataLR['25'])

#Scale data
sc = StandardScaler()
X1 = sc.fit_transform(X1)
X2 = sc.fit_transform(X2)

#run KNN on svm dataset
KNNSVM = KNeighborsClassifier(n_neighbors=750, n_jobs=-1)
scores = cross_val_score(estimator=KNNSVM, X=X1, y =y1, cv =cv, n_jobs=-1,verbose=1)
mean_scoreSVM = mean(scores)

print("Mean Score on SVM Dataset: ", mean_scoreSVM)

#run KNN on LR dataset
KNNLR = KNeighborsClassifier(n_neighbors=750, n_jobs=-1)
scores = cross_val_score(estimator=KNNLR, X=X2, y =y2, cv =cv, n_jobs=-1,verbose=1)
mean_scoreLR = mean(scores)

print("Mean Score on LR Dataset: ", mean_scoreLR)

[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:  8.9min finished


Mean Score on SVM Dataset:  0.7750216257847816


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:  8.9min finished


Mean Score on LR Dataset:  0.7791891704515973


## 3b. Artificial Neural Network

In [5]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import confusion_matrix as cm
from sklearn.metrics import accuracy_score as acc
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from statistics import mean
from sklearn.preprocessing import StandardScaler


dataLR = pd.read_csv('CancerImagesSingularValuesRFELR2.csv')
dataSVM = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')
cv = KFold(n_splits=5,random_state=1,shuffle=True)
X1 = np.array(dataSVM.iloc[:,0:16])
y1 = np.array(dataSVM['16'])

X2 = np.array(dataLR.iloc[:,0:25])
y2 = np.array(dataLR['25'])

sc = StandardScaler()
X1 = sc.fit_transform(X1)
X2 = sc.fit_transform(X2)
print("Running ---")
print()
ANN = MLPClassifier(max_iter=500,hidden_layer_sizes=(50,100,50),verbose=True)

scoresSVM = cross_val_score(estimator=ANN, X=X1, y =y1, cv =cv, n_jobs=-1,verbose=1)
scoresLR = cross_val_score(estimator=ANN, X=X2, y =y2, cv =cv, n_jobs=-1,verbose=1)

meanSVM = mean(scoresSVM)
meanLR = mean(scoresLR)

print("Mean Score SVM: {}".format(meanSVM))
print("Mean Score LR: {}".format(meanLR))

Running ---



[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:  7.6min finished
[Parallel(n_jobs=-1)]: Using backend LokyBackend with 16 concurrent workers.
[Parallel(n_jobs=-1)]: Done   5 out of   5 | elapsed:  7.7min finished


Mean Score SVM: 0.7689828651533889
Mean Score LR: 0.7705089201415687


## 3c. XGBoost 

In [6]:
from numpy import loadtxt
from sklearn.preprocessing import StandardScaler
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split, KFold, cross_val_score
from sklearn.metrics import accuracy_score
import pandas as pd
"""XGBoost Classifier with SVM"""
# Load csv file into a dataframe

bcdf = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')

#feature column names
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15']
#Declare features for unshuffled dataset
X = bcdf[feature_cols]
# Declare class for unshuffled df
y = bcdf['16']

# split data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=7)
scaler = StandardScaler()
# 5 folds selected
kfold = KFold(n_splits=5, random_state=1, shuffle=True)
# fit model on training data
model = XGBClassifier()
# Calculate cross validation score
results = cross_val_score(model, X, y, cv=kfold)
print("Accuracy with SVD: %.2f%% (%.2f%%)" % (results.mean()*100.0, results.std()*100.0))





"""XGBoost Classifier with RFELR """
# Load csv file into a dataframe

bcdf = pd.read_csv('CancerImagesSingularValuesRFELR2.csv')

#feature column names
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24']
#Declare features for unshuffled dataset
X2 = bcdf[feature_cols]
# Declare class for unshuffled df
y2 = bcdf['25']

# split data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X2, y2, test_size=0.2, random_state=7)
scaler = StandardScaler()
# 5 folds selected
kfold = KFold(n_splits=5, random_state=1, shuffle=True)
# fit model on training data
model = XGBClassifier()
# Calculate cross validation score
results2 = cross_val_score(model, X2, y2, cv=kfold)
print("Accuracy with LR: %.2f%% (%.2f%%)" % (results2.mean()*100.0, results2.std()*100.0))


Accuracy with SVD: 77.36% (0.24%)
Accuracy with LR: 77.75% (0.24%)


## 3d. Decision Tree

In [7]:
import numpy as np
import pandas as pd
from sklearn.tree import DecisionTreeClassifier

from sklearn.model_selection import train_test_split, KFold, cross_val_score
"""Decision tree classifier with SVD"""


# Load csv file into a dataframe
bcdf = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15']
X = bcdf[feature_cols]
y = bcdf['16']
# Training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size = 0.2,random_state=42)


# 5 folds selected
kfold = KFold(n_splits=5, random_state=1, shuffle=True)
# Call decision tree classifier using gini
clf_model = DecisionTreeClassifier(criterion="gini", random_state=42, max_depth=7, min_samples_leaf=8)

# Calculate cross validation score
results = cross_val_score(clf_model, X, y, cv=kfold)
print("Accuracy with SVD: %.3f%% (%.3f%%)" % (results.mean()*100.0, results.std()*100.0))


"""Decision Tree classifier with RFELR"""
# Load csv file into a dataframe

bcdf = pd.read_csv('CancerImagesSingularValuesRFELR2.csv')

#feature column names
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24']
#Declare features for dataset
X2 = bcdf[feature_cols]
# Declare class for  df
y2 = bcdf['25']
# Training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X2, y2, test_size = 0.2,random_state=42)
# 5 folds selected
kfold = KFold(n_splits=5, random_state=1, shuffle=True)
# Call decision tree classifier using gini
clf_model = DecisionTreeClassifier(criterion="gini", random_state=42, max_depth=7, min_samples_leaf=8)

# Calculate cross validation score
results2 = cross_val_score(clf_model, X2, y2, cv=kfold)
print("Accuracy with LR: %.3f%% (%.3f%%)" % (results2.mean()*100.0, results2.std()*100.0))


Accuracy with SVD: 76.694% (0.302%)
Accuracy with LR: 77.275% (0.247%)


## 3e. Logisitic Regression

### 3ea. Logisitic Regression Hyperparameter Tuning
#### Ensure the HyperParameterLR.py file is in the folder to run this section


In [34]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn.metrics import roc_curve, roc_auc_score, classification_report, accuracy_score, confusion_matrix, \
    plot_roc_curve
import matplotlib.pyplot as plt
from sklearn.utils import shuffle
from sklearn import linear_model, decomposition, datasets
from sklearn.model_selection import GridSearchCV

import sys

# Load csv file into a dataframe
from HyperParameterLR import std_slc, logistic_Reg

bcdf = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')

#feature column names
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15']
#Declare features for unshuffled dataset
X = bcdf[feature_cols]
# Declare class for unshuffled df
y = bcdf['16']

pca = decomposition.PCA()


pipe = Pipeline(steps=[('std_slc', std_slc),
                           ('pca', pca),
                           ('logistic_Reg', logistic_Reg)])

n_components = list(range(1, X.shape[1] + 1, 1))

C = np.logspace(-4, 4, 50)
penalty = ['l1', 'l2']

parameters = dict(pca__n_components=n_components,
                      logistic_Reg__C=C,
                      logistic_Reg__penalty=penalty)
# Use gridSearch CV to find hyperparameters
clf_GS = GridSearchCV(pipe, parameters)
clf_GS.fit(X, y)

print('Best Penalty:', clf_GS.best_estimator_.get_params()['logistic_Reg__penalty'])
print('Best C:', clf_GS.best_estimator_.get_params()['logistic_Reg__C'])
print('Best Number Of Components:', clf_GS.best_estimator_.get_params()['pca__n_components'])
print();
print(clf_GS.best_estimator_.get_params()['logistic_Reg'])


Best Penalty: l2
Best C: 1.2067926406393288
Best Number Of Components: 6

LogisticRegression(C=1.2067926406393288)


### 3eb. Training and Testing with Hyperparameters

In [11]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split, KFold, cross_val_score
from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn import linear_model, decomposition, datasets

"""Logistic regression using SVD feature Selected dataset"""

# Load csv file into a dataframe
bcdf = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')

#feature column names
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15']
#Declare features for unshuffled dataset
X = bcdf[feature_cols]
# Declare class for unshuffled df
y = bcdf['16']

pca = decomposition.PCA()




#Split train and test data (Unshuffled)
np.random.seed(42)
X_train, X_test, y_train, y_test = train_test_split(X, y)

"' Use Logistic regression model to predict accuracy"
scaler = StandardScaler()
# 5 folds selected
kfold = KFold(n_splits=5, random_state=1, shuffle=True)
# Call model with optimal hyperparameters
lr = LogisticRegression(C=1.2067926406393288, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=0, solver='liblinear', tol=0.0001, verbose=0,
                   warm_start=False)
"""model1 = Pipeline([('standardize', scaler),
                    ('log_reg', lr)])"""

# Calculate cross validation score
results = cross_val_score(lr, X, y, cv=kfold)
print("Accuracy with SVD: %.3f%% (%.3f%%)" % (results.mean()*100.0, results.std()*100.0))

"""Logistic regression using RFELR feature selected dataset"""

# read csv into a dataframe
bcdf = pd.read_csv('CancerImagesSingularValuesRFELR2.csv')

#feature column names
feature_cols = ['0', '1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '21', '22', '23', '24']
#Declare features for dataset
X2 = bcdf[feature_cols]
# Declare class for  df
y2 = bcdf['25']


#Split train and test data (Unshuffled)
np.random.seed(42)
X_train, X_test, y_train, y_test = train_test_split(X2, y2)

"' Use Logistic regression model to predict accuracy"
scaler = StandardScaler()
# 5 folds selected
kfold = KFold(n_splits=5, random_state=1, shuffle=True)
# Call model with optimal hyperparameters
lr = LogisticRegression(C=1.2067926406393288, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=0, solver='liblinear', tol=0.0001, verbose=0,
                   warm_start=False)
"""model1 = Pipeline([('standardize', scaler),
                    ('log_reg', lr)])"""

# Calculate cross validation score
results = cross_val_score(lr, X2, y2, cv=kfold)
print("Accuracy with LR: %.3f%% (%.3f%%)" % (results.mean()*100.0, results.std()*100.0))


Accuracy with SVD: 76.901% (0.175%)
Accuracy with LR: 77.020% (0.245%)


# Step 4: Generate FPR, FNR, and ROC Curve

In [12]:
from sklearn.metrics import confusion_matrix as cm
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.metrics import confusion_matrix as cm
from sklearn.metrics import accuracy_score as acc
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from statistics import mean
from sklearn.preprocessing import StandardScaler

## 4a. KNN

In [13]:
dataLR = pd.read_csv('CancerImagesSingularValuesRFELR2.csv')
dataSVM = pd.read_csv('CancerImagesSVDwithFeaturesSelected.csv')
cv = KFold(n_splits=10,random_state=1,shuffle=True)
X1 = np.array(dataSVM.iloc[:,0:16])
y1 = np.array(dataSVM['16'])

X2 = np.array(dataLR.iloc[:,0:25])
y2 = np.array(dataLR['25'])

sc = StandardScaler()
X1 = sc.fit_transform(X1)
X2 = sc.fit_transform(X2)

X1_train, X1_test, y1_train, y1_test = train_test_split(X1,y1, test_size= 0.2, random_state=1, shuffle = True)
X2_train, X2_test, y2_train, y2_test = train_test_split(X1,y1, test_size= 0.2, random_state=1, shuffle = True)
KNNSVM = KNeighborsClassifier(n_neighbors=750, n_jobs=-1).fit(X1_train,y1_train)
KNNLR = KNeighborsClassifier(n_neighbors=750, n_jobs=-1).fit(X2_train,y2_train)
predictSVM = KNNSVM.predict(X1_test)
predictLR = KNNSVM.predict(X2_test)
cmatrixSVM = cm(y1_test, predictSVM)
cmatrixLR = cm(y2_test,predictLR)

In [14]:
# get the confusion matrix and compute fnr and fpr
predictSVM = KNNSVM.predict(X1_test)
predictLR = KNNLR.predict(X2_test)
cmatrixSVM = cm(y1_test, predictSVM)
cmatrixLR = cm(y2_test,predictLR)

#confusion matrix and fnr/fpr for SVM
tp,fp,fn,tn = cmatrixSVM.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for SVM Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for SVM Dataset: {}%".format(fnr))

#confusion matrix and fnr/fpr for LR
tp,fp,fn,tn = cmatrixLR.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for LR Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for LR Dataset: {}%".format(fnr))

False Postive Rate for SVM Dataset: 36.46771613772203%
False negative Rate for SVM Dataset: 19.102997729694668%
False Postive Rate for LR Dataset: 36.46771613772203%
False negative Rate for LR Dataset: 19.102997729694668%


In [15]:
#predict Probabilites
KNNprobSVM = KNNSVM.predict_proba(X1_test)[:,1]
KNNprobLR = KNNLR.predict_proba(X2_test)[:,1]

## 4b. ANN

In [16]:
 import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import confusion_matrix as cm
from sklearn.metrics import accuracy_score as acc
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score
from statistics import mean
from sklearn.preprocessing import StandardScaler

#fit model
ANNSVM = MLPClassifier(max_iter=500,hidden_layer_sizes=(50,100,50)).fit(X1_train,y1_train)
ANNLR = MLPClassifier(max_iter=500,hidden_layer_sizes=(50,100,50)).fit(X2_train,y2_train)

In [17]:
# get the confusion matrix and compute fnr and fpr
predictSVM = ANNSVM.predict(X1_test)
predictLR = ANNLR.predict(X2_test)
cmatrixSVM = cm(y1_test, predictSVM)
cmatrixLR = cm(y2_test,predictLR)

#confusion matrix and fnr/fpr for SVM
tp,fp,fn,tn = cmatrixSVM.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for SVM Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for SVM Dataset: {}%".format(fnr))

#confusion matrix and fnr/fpr for LR
tp,fp,fn,tn = cmatrixLR.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for LR Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for LR Dataset: {}%".format(fnr))

False Postive Rate for SVM Dataset: 36.499732667973625%
False negative Rate for SVM Dataset: 19.77728590009812%
False Postive Rate for LR Dataset: 36.13201094391245%
False negative Rate for LR Dataset: 19.19998154513368%


In [18]:
#get probabilities
ANNprobSVM = ANNSVM.predict_proba(X1_test)[:,1]
ANNprobLR = ANNLR.predict_proba(X2_test)[:,1]

## 4c. XGBoost

In [19]:
from numpy import loadtxt
from sklearn.preprocessing import StandardScaler
from xgboost import XGBClassifier
from sklearn.model_selection import train_test_split, KFold, cross_val_score
from sklearn.metrics import accuracy_score
import pandas as pd

#fit model
XGBSVM = XGBClassifier().fit(X1_train,y1_train)
XGBLR = XGBClassifier().fit(X2_train,y2_train)

In [20]:
# get the confusion matrix and compute fnr and fpr
predictSVM = XGBSVM.predict(X1_test)
predictLR = XGBLR.predict(X2_test)
cmatrixSVM = cm(y1_test, predictSVM)
cmatrixLR = cm(y2_test,predictLR)

#confusion matrix and fnr/fpr for SVM
tp,fp,fn,tn = cmatrixSVM.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for SVM Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for SVM Dataset: {}%".format(fnr))

#confusion matrix and fnr/fpr for LR
tp,fp,fn,tn = cmatrixLR.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for LR Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for LR Dataset: {}%".format(fnr))

False Postive Rate for SVM Dataset: 36.50780044573976%
False negative Rate for SVM Dataset: 19.331934807164757%
False Postive Rate for LR Dataset: 36.50780044573976%
False negative Rate for LR Dataset: 19.331934807164757%


In [21]:
#get probabilities
XGBprobSVM = XGBSVM.predict_proba(X1_test)[:,1]
XGBprobLR = XGBLR.predict_proba(X2_test)[:,1]

## 4d. Decision Tree

In [22]:
import numpy as np
import pandas as pd
from sklearn.tree import DecisionTreeClassifier

#fit model
DTCSVM = DecisionTreeClassifier(criterion="gini", random_state=42, max_depth=7, min_samples_leaf=8).fit(X1_train,y1_train)
DTCLR = DecisionTreeClassifier(criterion="gini", random_state=42, max_depth=7, min_samples_leaf=8).fit(X2_train,y2_train)

In [23]:
# get the confusion matrix and compute fnr and fpr
predictSVM = DTCSVM.predict(X1_test)
predictLR = DTCLR.predict(X2_test)
cmatrixSVM = cm(y1_test, predictSVM)
cmatrixLR = cm(y2_test,predictLR)

#confusion matrix and fnr/fpr for SVM
tp,fp,fn,tn = cmatrixSVM.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for SVM Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for SVM Dataset: {}%".format(fnr))

#confusion matrix and fnr/fpr for LR
tp,fp,fn,tn = cmatrixLR.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for LR Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for LR Dataset: {}%".format(fnr))

False Postive Rate for SVM Dataset: 38.65092748735244%
False negative Rate for SVM Dataset: 19.722125738103507%
False Postive Rate for LR Dataset: 38.65092748735244%
False negative Rate for LR Dataset: 19.722125738103507%


In [24]:
#get probabilities
DTCprobSVM = DTCSVM.predict_proba(X1_test)[:,1]
DTCprobLR = DTCLR.predict_proba(X2_test)[:,1]

## 4e. Logistic Regression

In [25]:
from sklearn.linear_model import LogisticRegression
#fit model
LRCSVM = LogisticRegression(C=1.2067926406393288, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=0, solver='liblinear', tol=0.0001, verbose=0,
                   warm_start=False).fit(X1_train,y1_train)

LRCLR = LogisticRegression(C=1.2067926406393288, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None,
                   multi_class='auto', n_jobs=None, penalty='l2',
                   random_state=0, solver='liblinear', tol=0.0001, verbose=0,
                   warm_start=False).fit(X2_train,y2_train)

In [26]:
# get the confusion matrix and compute fnr and fpr
predictSVM = LRCSVM.predict(X1_test)
predictLR = LRCLR.predict(X2_test)
cmatrixSVM = cm(y1_test, predictSVM)
cmatrixLR = cm(y2_test,predictLR)

#confusion matrix and fnr/fpr for SVM
tp,fp,fn,tn = cmatrixSVM.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for SVM Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for SVM Dataset: {}%".format(fnr))

#confusion matrix and fnr/fpr for LR
tp,fp,fn,tn = cmatrixLR.ravel()
acc = ((tp+tn) / (tn+fp+tp+fn))*100
fpr = (fp / (fp+tn))*100
print("False Postive Rate for LR Dataset: {}%".format(fpr))
fnr = (fn / (fn+tp))*100
print("False negative Rate for LR Dataset: {}%".format(fnr))

False Postive Rate for SVM Dataset: 37.24016785400605%
False negative Rate for SVM Dataset: 20.898254386356534%
False Postive Rate for LR Dataset: 37.24016785400605%
False negative Rate for LR Dataset: 20.898254386356534%


In [27]:
#get probabilities
LRCprobSVM = LRCSVM.predict_proba(X1_test)[:,1]
LRCprobLR = LRCLR.predict_proba(X2_test)[:,1]

## 4f. Plot SVM ROC Curve

In [28]:
import matplotlib.pyplot as plt
from sklearn.metrics import roc_curve as roc
from sklearn.metrics import roc_auc_score as auc

KNNfpr, KNNtpr, _ = roc(y1_test,KNNprobSVM)
KNNauc = auc(y1_test,KNNprobSVM)

ANNfpr, ANNtpr, _ = roc(y1_test,ANNprobSVM)
ANNauc = auc(y1_test,ANNprobSVM)

XGBfpr, XGBtpr, _ = roc(y1_test,XGBprobSVM)
XGBauc = auc(y1_test,XGBprobSVM)

DTCfpr, DTCtpr, _ = roc(y1_test,DTCprobSVM)
DTCauc = auc(y1_test,DTCprobSVM)

LRCfpr, LRCtpr, _ = roc(y1_test,LRCprobSVM)
LRCauc = auc(y1_test,LRCprobSVM)
plt.figure(dpi=1080,figsize =(16,9),facecolor='white')
plt.plot(KNNfpr,KNNtpr,label="KNN auc=%0.2f" %KNNauc)
plt.plot(ANNfpr,ANNtpr,label="ANN auc=%0.2f" %ANNauc)
plt.plot(XGBfpr,XGBtpr,label="XGB auc=%0.2f" %XGBauc)
plt.plot(DTCfpr,DTCtpr,label="DTC auc=%0.2f" %DTCauc)
plt.plot(LRCfpr,LRCtpr,label="LRC auc=%0.2f" %LRCauc)
plt.plot()
plt.legend(loc = 'lower right',fontsize=20)
plt.plot([0, 1], [0, 1],'r--')
plt.ylabel('True Positive Rate',fontsize=20)
plt.yticks(fontsize=15)
plt.xticks(fontsize=15)
plt.xlabel('False Positive Rate',fontsize=20)
plt.title('Reciever Operating Characteristic Curve for RFE with SVM Dataset',fontsize = 20)
plt.savefig('ROCCurveSVM.png')

## 4e. Plot LR ROC Curve

In [29]:
import matplotlib.pyplot as plt
from sklearn.metrics import roc_curve as roc
from sklearn.metrics import roc_auc_score as auc

KNNfpr, KNNtpr, _ = roc(y2_test,KNNprobLR)
KNNauc = auc(y2_test,KNNprobLR)

ANNfpr, ANNtpr, _ = roc(y2_test,ANNprobLR)
ANNauc = auc(y2_test,ANNprobLR)

XGBfpr, XGBtpr, _ = roc(y2_test,XGBprobLR)
XGBauc = auc(y2_test,XGBprobLR)

DTCfpr, DTCtpr, _ = roc(y2_test,DTCprobLR)
DTCauc = auc(y2_test,DTCprobLR)

LRCfpr, LRCtpr, _ = roc(y2_test,LRCprobLR)
LRCauc = auc(y2_test,LRCprobLR)
plt.figure(dpi=1080,figsize =(16,9),facecolor='white')
plt.plot(KNNfpr,KNNtpr,label="KNN auc=%0.2f" %KNNauc)
plt.plot(ANNfpr,ANNtpr,label="ANN auc=%0.2f" %ANNauc)
plt.plot(XGBfpr,XGBtpr,label="XGB auc=%0.2f" %XGBauc)
plt.plot(DTCfpr,DTCtpr,label="DTC auc=%0.2f" %DTCauc)
plt.plot(LRCfpr,LRCtpr,label="LRC auc=%0.2f" %LRCauc)
plt.plot()
plt.legend(loc = 'lower right',fontsize=20)
plt.plot([0, 1], [0, 1],'r--')
plt.ylabel('True Positive Rate',fontsize=20)
plt.yticks(fontsize=15)
plt.xticks(fontsize=15)
plt.xlabel('False Positive Rate',fontsize=20)
plt.title('Reciever Operating Characteristic Curve for RFE with LR Dataset',fontsize = 20)
plt.savefig('ROCCurveLR.png')

# Thank You 